<a href="https://colab.research.google.com/github/unreal-kz/Notes/blob/master/FineTuneSAM_SEG_ECHO.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [16]:
!python -m torch.utils.collect_env

PyTorch version: 2.1.2+cu121
Is debug build: False
CUDA used to build PyTorch: 12.1
ROCM used to build PyTorch: N/A

OS: Microsoft Windows 11 Home
GCC version: Could not collect
Clang version: Could not collect
CMake version: Could not collect
Libc version: N/A

Python version: 3.9.18 (main, Sep 11 2023, 14:09:26) [MSC v.1916 64 bit (AMD64)] (64-bit runtime)
Python platform: Windows-10-10.0.22621-SP0
Is CUDA available: True
CUDA runtime version: 12.3.107

CUDA_MODULE_LOADING set to: LAZY
GPU models and configuration: GPU 0: NVIDIA GeForce RTX 3080 Ti
Nvidia driver version: 551.23
cuDNN version: C:\Program Files\NVIDIA GPU Computing Toolkit\CUDA\v12.3\bin\cudnn_ops_train64_8.dll
HIP runtime version: N/A
MIOpen runtime version: N/A
Is XNNPACK available: True

CPU:
Architecture=9


CurrentClockSpeed=3504


DeviceID=CPU0


Family=207


L2CacheSize=4096


L2CacheSpeed=


Manufacturer=GenuineIntel


MaxClockSpeed=3504


Name=11th Gen Intel(R) Core(TM) i9-11900KF @ 3.50GHz


ProcessorType=3



In [17]:
import torch

In [18]:
a=torch.cuda.FloatTensor()

In [19]:
# !pip uninstall torch

In [20]:
!pip install -q transformers datasets segments-ai evaluate
!pip install -U accelerate
!pip install -U transformers

In [21]:
# !pip3 install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu121

In [22]:
print(torch.backends.cudnn.enabled)

True


In [23]:
print(torch.cuda.is_available())

True


In [24]:
import torch

# List all available GPUs
if torch.cuda.is_available():
    print("Available CUDA Devices:")
    for i in range(torch.cuda.device_count()):
        print(f"Device {i}: {torch.cuda.get_device_name(i)}")
else:
    print("No CUDA devices are available")

# Check CUDA_VISIBLE_DEVICES environment variable
import os
cuda_visible_devices = os.getenv('CUDA_VISIBLE_DEVICES')
print("CUDA_VISIBLE_DEVICES:", cuda_visible_devices if cuda_visible_devices is not None else "Not set (All GPUs are visible)")


Available CUDA Devices:
Device 0: NVIDIA GeForce RTX 3080 Ti
CUDA_VISIBLE_DEVICES: Not set (All GPUs are visible)


In [25]:
from huggingface_hub import notebook_login

notebook_login()

In [26]:
# # fc54be4c5ea286d6edd6ad27a963a73a91e5ab1b
from segments import SegmentsClient
from getpass import getpass

api_key = getpass('Enter your API key: ')
segments_client = SegmentsClient(api_key)

In [27]:
# from segments.huggingface import release2dataset

# # dataset_identifier = 'label_h/Test_seg'
# dataset_identifier = 'ai_segment/Real_ECHO_Dateset'
# release_name = 'v0.3_full_label' #'v0.1_9_lbls'

# release = segments_client.get_release(dataset_identifier, release_name)
# hf_dataset = release2dataset(release)

In [28]:
# hf_dataset

In [29]:
# from segments.utils import get_semantic_bitmap


# def convert_segmentation_bitmap(example):
#     return {
#         "label.segmentation_bitmap":
#             get_semantic_bitmap(
#                 example["label.segmentation_bitmap"],
#                 example["label.annotations"],
#             )
#     }


# semantic_dataset = hf_dataset.map(
#     convert_segmentation_bitmap,
# )

In [30]:
# semantic_dataset = semantic_dataset.rename_column('image', 'pixel_values')
# semantic_dataset = semantic_dataset.rename_column('label.segmentation_bitmap', 'label')
# semantic_dataset = semantic_dataset.remove_columns(['name', 'uuid', 'status', 'label.annotations'])

In [31]:
hf_dataset_identifier = "unreal-hug/REAL_DATASET_SEG_401_6_lbls"
# semantic_dataset.push_to_hub(hf_dataset_identifier)

In [32]:
from datasets import load_dataset

ds = load_dataset(hf_dataset_identifier)

In [33]:
ds = ds.shuffle(seed=1)
ds = ds["train"].train_test_split(test_size=0.2)
train_ds = ds["train"]
test_ds = ds["test"]

In [34]:
import json
from huggingface_hub import hf_hub_download

filename = "id2label.json"
id2label = json.load(open(hf_hub_download(repo_id=hf_dataset_identifier, filename=filename, repo_type="dataset"), "r"))
id2label = {int(k): v for k, v in id2label.items()}
label2id = {v: k for k, v in id2label.items()}

num_labels = len(id2label)
print("Id2label:", id2label)

Id2label: {0: 'unlabeled', 1: 'LV', 2: 'RV', 3: 'RA', 4: 'LA', 5: 'VS', 6: 'AS', 7: 'MK', 8: 'TK', 9: 'ASD', 10: 'VSD', 11: 'AK'}


In [35]:
from torchvision.transforms import ColorJitter
from transformers import (
    SegformerImageProcessor,
)

processor = SegformerImageProcessor()
jitter = ColorJitter(brightness=0.25, contrast=0.25, saturation=0.25, hue=0.1)

def train_transforms(example_batch):
    images = [jitter(x) for x in example_batch['pixel_values']]
    labels = [x for x in example_batch['label']]
    inputs = processor(images, labels)
    return inputs


def val_transforms(example_batch):
    images = [x for x in example_batch['pixel_values']]
    labels = [x for x in example_batch['label']]
    inputs = processor(images, labels)
    return inputs


# Set transforms
train_ds.set_transform(train_transforms)
test_ds.set_transform(val_transforms)

In [36]:
from transformers import SegformerForSemanticSegmentation

pretrained_model_name = "nvidia/mit-b0"
model = SegformerForSemanticSegmentation.from_pretrained(
    pretrained_model_name,
    id2label=id2label,
    label2id=label2id
)

device = "cuda" if torch.cuda.is_available() else "cpu"
model.to(device)  # Move your model to the selected device


c:\Users\rogbeast\anaconda3\envs\hugging_face\lib\site-packages\torch\_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Some weights of SegformerForSemanticSegmentation were not initialized from the model checkpoint at nvidia/mit-b0 and are newly initialized: ['decode_head.batch_norm.bias', 'decode_head.batch_norm.num_batches_tracked', 'decode_head.batch_norm.running_mean', 'decode_head.batch_norm.running_var', 'decode_head.batch_norm.weight', 'decode_head.classifier.bias', 'decode_head.classifier.weight', 'decode_head.linear_c.0.proj.bias', 'decode_head.linear_c.0.proj.weight', 'decode_head.linear_c.1.proj.bias', 'decode_head.linear_c.1.proj.weight', 'decode_head.linear_c.2.proj.bias', 'decode_

SegformerForSemanticSegmentation(
  (segformer): SegformerModel(
    (encoder): SegformerEncoder(
      (patch_embeddings): ModuleList(
        (0): SegformerOverlapPatchEmbeddings(
          (proj): Conv2d(3, 32, kernel_size=(7, 7), stride=(4, 4), padding=(3, 3))
          (layer_norm): LayerNorm((32,), eps=1e-05, elementwise_affine=True)
        )
        (1): SegformerOverlapPatchEmbeddings(
          (proj): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
          (layer_norm): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
        )
        (2): SegformerOverlapPatchEmbeddings(
          (proj): Conv2d(64, 160, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
          (layer_norm): LayerNorm((160,), eps=1e-05, elementwise_affine=True)
        )
        (3): SegformerOverlapPatchEmbeddings(
          (proj): Conv2d(160, 256, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
          (layer_norm): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
  

In [37]:
from transformers import TrainingArguments

epochs = 25
lr = 0.0001
batch_size = 2

hub_model_id = "segformer-b0-finetuned-segments-ECHO-feb-13-v1"

training_args = TrainingArguments(
    "segformer-b0-finetuned-segments-outputs",
    learning_rate=lr,
    num_train_epochs=epochs,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    save_total_limit=3,
    evaluation_strategy="steps",
    save_strategy="steps",
    save_steps=20,
    eval_steps=20,
    logging_steps=1,
    eval_accumulation_steps=5,
    load_best_model_at_end=True,
    push_to_hub=True,
    hub_model_id=hub_model_id,

    hub_strategy="end",
)

In [38]:
import torch
from torch import nn
import evaluate
import multiprocessing

metric = evaluate.load("mean_iou")

def compute_metrics(eval_pred):
  with torch.no_grad():
    logits, labels = eval_pred
    logits_tensor = torch.from_numpy(logits)
    # scale the logits to the size of the label
    logits_tensor = nn.functional.interpolate(
        logits_tensor,
        size=labels.shape[-2:],
        mode="bilinear",
        align_corners=False,
    ).argmax(dim=1)

    pred_labels = logits_tensor.detach().cpu().numpy()
    metrics = metric._compute(
            predictions=pred_labels,
            references=labels,
            num_labels=len(id2label),
            ignore_index=0,
            reduce_labels=processor.do_reduce_labels,
        )

    # add per category metrics as individual key-value pairs
    per_category_accuracy = metrics.pop("per_category_accuracy").tolist()
    per_category_iou = metrics.pop("per_category_iou").tolist()

    metrics.update({f"accuracy_{id2label[i]}": v for i, v in enumerate(per_category_accuracy)})
    metrics.update({f"iou_{id2label[i]}": v for i, v in enumerate(per_category_iou)})

    return metrics

In [39]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_ds,
    eval_dataset=test_ds,
    compute_metrics=compute_metrics,
)

In [40]:
trainer.train()

  0%|          | 0/4000 [00:00<?, ?it/s]

{'loss': 2.3473, 'learning_rate': 9.9975e-05, 'epoch': 0.01}
{'loss': 2.2622, 'learning_rate': 9.995e-05, 'epoch': 0.01}
{'loss': 2.2357, 'learning_rate': 9.9925e-05, 'epoch': 0.02}
{'loss': 2.2034, 'learning_rate': 9.99e-05, 'epoch': 0.03}
{'loss': 2.1585, 'learning_rate': 9.9875e-05, 'epoch': 0.03}
{'loss': 2.1904, 'learning_rate': 9.985000000000001e-05, 'epoch': 0.04}
{'loss': 2.1492, 'learning_rate': 9.9825e-05, 'epoch': 0.04}
{'loss': 2.0709, 'learning_rate': 9.98e-05, 'epoch': 0.05}
{'loss': 2.074, 'learning_rate': 9.977500000000001e-05, 'epoch': 0.06}
{'loss': 2.0431, 'learning_rate': 9.975000000000001e-05, 'epoch': 0.06}
{'loss': 1.9408, 'learning_rate': 9.9725e-05, 'epoch': 0.07}
{'loss': 1.9906, 'learning_rate': 9.970000000000001e-05, 'epoch': 0.07}
{'loss': 1.8631, 'learning_rate': 9.967500000000001e-05, 'epoch': 0.08}
{'loss': 1.8883, 'learning_rate': 9.965000000000001e-05, 'epoch': 0.09}
{'loss': 1.9316, 'learning_rate': 9.9625e-05, 'epoch': 0.09}
{'loss': 1.8542, 'learnin

  0%|          | 0/41 [00:00<?, ?it/s]

C:\Users\rogbeast\.cache\huggingface\modules\evaluate_modules\metrics\evaluate-metric--mean_iou\08bc20f4f895f3caf75fb9e3fada1404bded3c3265243d05327cbb3b9326ffe9\mean_iou.py:259: RuntimeWarning: invalid value encountered in divide
  iou = total_area_intersect / total_area_union
C:\Users\rogbeast\.cache\huggingface\modules\evaluate_modules\metrics\evaluate-metric--mean_iou\08bc20f4f895f3caf75fb9e3fada1404bded3c3265243d05327cbb3b9326ffe9\mean_iou.py:260: RuntimeWarning: invalid value encountered in divide
  acc = total_area_intersect / total_area_label
Checkpoint destination directory segformer-b0-finetuned-segments-outputs\checkpoint-20 already exists and is non-empty.Saving will proceed but saved results may be invalid.


{'eval_loss': 1.988379955291748, 'eval_mean_iou': 0.08309316723217665, 'eval_mean_accuracy': 0.12846487983660576, 'eval_overall_accuracy': 0.22557309597328942, 'eval_accuracy_unlabeled': nan, 'eval_accuracy_LV': 0.35013841614934627, 'eval_accuracy_RV': 0.0, 'eval_accuracy_RA': 0.012044741068330199, 'eval_accuracy_LA': 0.35264374755589706, 'eval_accuracy_VS': 0.0, 'eval_accuracy_AS': 0.0, 'eval_accuracy_MK': 0.0, 'eval_accuracy_TK': nan, 'eval_accuracy_ASD': 0.0021921911085450345, 'eval_accuracy_VSD': 0.12712537859477613, 'eval_accuracy_AK': 0.440504323889163, 'eval_iou_unlabeled': 0.0, 'eval_iou_LV': 0.2520954482728996, 'eval_iou_RV': 0.0, 'eval_iou_RA': 0.01194566224390361, 'eval_iou_LA': 0.22483184414294916, 'eval_iou_VS': 0.0, 'eval_iou_AS': 0.0, 'eval_iou_MK': 0.0, 'eval_iou_TK': nan, 'eval_iou_ASD': 0.0021799587332914684, 'eval_iou_VSD': 0.08716728181191977, 'eval_iou_AK': 0.3358046443489795, 'eval_runtime': 4.9744, 'eval_samples_per_second': 16.283, 'eval_steps_per_second': 8.242

...

{'eval_loss': 0.403333455324173, 'eval_mean_iou': 0.3147717573626251, 'eval_mean_accuracy': 0.3733777878494031, 'eval_overall_accuracy': 0.5793443639251394, 'eval_accuracy_unlabeled': nan, 'eval_accuracy_LV': 0.6963711998949946, 'eval_accuracy_RV': 0.42839186725354056, 'eval_accuracy_RA': 0.5617913374706447, 'eval_accuracy_LA': 0.6673653084886697, 'eval_accuracy_VS': 0.011642578573067218, 'eval_accuracy_AS': 0.0, 'eval_accuracy_MK': 0.06480011545677587, 'eval_accuracy_TK': nan, 'eval_accuracy_ASD': 0.4160291570438799, 'eval_accuracy_VSD': 0.3538924041143131, 'eval_accuracy_AK': 0.5334939101981457, 'eval_iou_unlabeled': 0.0, 'eval_iou_LV': 0.6661575230077763, 'eval_iou_RV': 0.418041993650033, 'eval_iou_RA': 0.5356132315913187, 'eval_iou_LA': 0.6171995082682318, 'eval_iou_VS': 0.011433399042523234, 'eval_iou_AS': 0.0, 'eval_iou_MK': 0.06101268832911522, 'eval_iou_TK': nan, 'eval_iou_ASD': 0.3431632994753879, 'eval_iou_VSD': 0.32636200221238937, 'eval_iou_AK': 0.4835056854121004, 'eval_ru

  0%|          | 0/41 [00:00<?, ?it/s]

C:\Users\rogbeast\.cache\huggingface\modules\evaluate_modules\metrics\evaluate-metric--mean_iou\08bc20f4f895f3caf75fb9e3fada1404bded3c3265243d05327cbb3b9326ffe9\mean_iou.py:259: RuntimeWarning: invalid value encountered in divide
  iou = total_area_intersect / total_area_union
C:\Users\rogbeast\.cache\huggingface\modules\evaluate_modules\metrics\evaluate-metric--mean_iou\08bc20f4f895f3caf75fb9e3fada1404bded3c3265243d05327cbb3b9326ffe9\mean_iou.py:260: RuntimeWarning: invalid value encountered in divide
  acc = total_area_intersect / total_area_label


{'eval_loss': 0.4015546143054962, 'eval_mean_iou': 0.30150523136095164, 'eval_mean_accuracy': 0.3540808657554819, 'eval_overall_accuracy': 0.5682075630924895, 'eval_accuracy_unlabeled': nan, 'eval_accuracy_LV': 0.7085519701927981, 'eval_accuracy_RV': 0.44793642608519496, 'eval_accuracy_RA': 0.5530311589583013, 'eval_accuracy_LA': 0.6067429798503008, 'eval_accuracy_VS': 0.011527873365450792, 'eval_accuracy_AS': 0.0, 'eval_accuracy_MK': 0.0517931880502237, 'eval_accuracy_TK': nan, 'eval_accuracy_ASD': 0.3590051241339492, 'eval_accuracy_VSD': 0.33829130056676765, 'eval_accuracy_AK': 0.4639286363518321, 'eval_iou_unlabeled': 0.0, 'eval_iou_LV': 0.6787351522265141, 'eval_iou_RV': 0.4363967476951876, 'eval_iou_RA': 0.5180791206049621, 'eval_iou_LA': 0.5726345335759286, 'eval_iou_VS': 0.011352725218864728, 'eval_iou_AS': 0.0, 'eval_iou_MK': 0.04883649724433558, 'eval_iou_TK': nan, 'eval_iou_ASD': 0.30455978693442726, 'eval_iou_VSD': 0.31275948349355753, 'eval_iou_AK': 0.4332034979766903, 'eva

  0%|          | 0/41 [00:00<?, ?it/s]

In [ ]:
kwargs = {
    "tags": ["vision", "image-segmentation"],
    "finetuned_from": pretrained_model_name,
    "dataset": hf_dataset_identifier,
}

processor.push_to_hub(hub_model_id)
trainer.push_to_hub(**kwargs)

In [ ]:
from transformers import SegformerImageProcessor, SegformerForSemanticSegmentation

processor = SegformerImageProcessor.from_pretrained("nvidia/segformer-b0-finetuned-ade-512-512")
model = SegformerForSemanticSegmentation.from_pretrained(f"unreal-hug/{hub_model_id}")